In [1]:
import matplotlib as mat
import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sns
import numpy as np
import time

pd.set_option('display.max_rows', 100)
pd.set_option('display.max_columns', 100)
mat.rcParams['agg.path.chunksize'] = 1000000000000

from matplotlib import style
style.use('fivethirtyeight')
%matplotlib inline

In [2]:
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import minmax_scale, LabelEncoder
from sklearn.metrics import accuracy_score
from catboost import CatBoostClassifier, Pool

from imblearn.over_sampling import RandomOverSampler

In [3]:
DIR_NAME = "zipfilee_FILES/ds_data/"
TRAIN_FILE = "data_train.csv"
TEST_FILE = "data_test.csv"

In [4]:
train = pd.read_csv(DIR_NAME+TRAIN_FILE)
test = pd.read_csv(DIR_NAME+TEST_FILE)

In [5]:
#too many unique values as well as too many missing values, let's remove it
train.drop('num18', axis=1, inplace=True)
#too many missing values, and less categories, lets make the missing as another category, here 88,99 and 66 for example.
train.cat6.fillna(88, inplace=True)
train.cat8.fillna(99, inplace=True)
train.cat10.fillna(66, inplace=True)
#Replace these categories with the most frequent label.
agg_cat = ["cat1", "cat2", "cat3", "cat4", "cat5", "cat12"]
for i in agg_cat:
    max_ = train[i].value_counts()
    for j in max_.index:
        if max_[j] == max_.max():
            val = j
    train[i].fillna(j, inplace=True)
    print(i, " completed!")
#The rest less missing values
train.fillna(-999, inplace=True)

#---------------------------------------------------------------------------------------------------------------------------
#doing the same with test features
#too many unique values as well as too many missing values, let's remove it
test.drop('num18', axis=1, inplace=True)
#too many missing values, and less categories, lets make the missing as another category, here 88,99 and 66 for example.
test.cat6.fillna(88, inplace=True)
test.cat8.fillna(99, inplace=True)
test.cat10.fillna(66, inplace=True)
#Replace these categories with the most frequent label.
agg_cat = ["cat1", "cat2", "cat3", "cat4", "cat5", "cat12"]
for i in agg_cat:
    max_ = train[i].value_counts()
    for j in max_.index:
        if max_[j] == max_.max():
            val = j
    train[i].fillna(j, inplace=True)
    print(i, " completed!")
#The rest less missing values
train.fillna(-999, inplace=True)

cat1  completed!
cat2  completed!
cat3  completed!
cat4  completed!
cat5  completed!
cat12  completed!
cat1  completed!
cat2  completed!
cat3  completed!
cat4  completed!
cat5  completed!
cat12  completed!


In [6]:
print(train.shape)
print(test.shape)

(596000, 57)
(892816, 56)


In [7]:
print(train.columns)

Index(['id', 'num1', 'num2', 'num3', 'num4', 'num5', 'num6', 'num7', 'num8',
       'num9', 'num10', 'num11', 'num12', 'num13', 'num14', 'num15', 'num16',
       'num17', 'num19', 'num20', 'num21', 'num22', 'num23', 'der1', 'der2',
       'der3', 'der4', 'der5', 'der6', 'der7', 'der8', 'der9', 'der10',
       'der11', 'der12', 'der13', 'der14', 'der15', 'der16', 'der17', 'der18',
       'der19', 'cat1', 'cat2', 'cat3', 'cat4', 'cat5', 'cat6', 'cat7', 'cat8',
       'cat9', 'cat10', 'cat11', 'cat12', 'cat13', 'cat14', 'target'],
      dtype='object')

In [8]:
col1 = ['num1', 'num2', 'num3', 'num4', 'num5', 'num6', 'num7', 'num8',
       'num9', 'num10', 'num11', 'num12', 'num13', 'num14', 'num15', 'num16',
       'num17', 'num19', 'num20', 'num21', 'num22', 'num23', 'der1', 'der2',
       'der3', 'der4', 'der5', 'der6', 'der7', 'der8', 'der9', 'der10',
       'der11', 'der12', 'der13', 'der14', 'der15', 'der16', 'der17', 'der18',
       'der19']
col2 = ['cat1', 'cat2', 'cat3', 'cat4', 'cat5', 'cat6', 'cat7', 'cat8',
       'cat9', 'cat10', 'cat11', 'cat12', 'cat13', 'cat14']

train[col1] = minmax_scale(train[col1])
test[col1] = minmax_scale(test[col1])

/home/ashu2_gamer/.local/lib/python3.5/site-packages/ipykernel_launcher.py:10: DataConversionWarning: Data with input dtype int64, float64 were all converted to float64.
  # Remove the CWD from sys.path while we load stuff.
/home/ashu2_gamer/.local/lib/python3.5/site-packages/ipykernel_launcher.py:11: DataConversionWarning: Data with input dtype int64, float64 were all converted to float64.
  # This is added back by InteractiveShellApp.init_path()


In [9]:
le = LabelEncoder()
for i in col2:
    train[i] = le.fit_transform(train[i])
    test[i] = le.fit_transform(test[i])

y = train.target
train.drop(["target", "id"], axis=1, inplace=True)
test.drop("id", axis=1, inplace=True)
x_train, x_val, y_train, y_val = train_test_split(train, y, test_size=0.1)
print(x_train.shape , " and ", y_train.shape)
print(x_val.shape, " and ", y_val.shape)
print(test.shape)

(536400, 55)  and  (536400,)
(59600, 55)  and  (59600,)
(892816, 55)


In [10]:
ros = RandomOverSampler(random_state=0)
ros.fit(x_train, y_train)
X_resampledo, y_resampledo = ros.fit_sample(x_train, y_train)

In [11]:
catboost_pool = Pool(X_resampledo, y_resampledo)
cat_model = CatBoostClassifier(task_type='GPU', iterations=50000, learning_rate=0.01, early_stopping_rounds=5)
cat_model.fit(X_resampledo, y_resampledo, verbose=3, plot=False, eval_set=(x_val, y_val),)

0:	learn: 0.6927486	test: 0.6927560	best: 0.6927560 (0)	total: 35.8ms	remaining: 29m 51s
1:	learn: 0.6923593	test: 0.6923763	best: 0.6923763 (1)	total: 70.6ms	remaining: 29m 23s
2:	learn: 0.6919780	test: 0.6920040	best: 0.6920040 (2)	total: 105ms	remaining: 29m 10s
3:	learn: 0.6916025	test: 0.6916297	best: 0.6916297 (3)	total: 140ms	remaining: 29m 11s
4:	learn: 0.6912361	test: 0.6912710	best: 0.6912710 (4)	total: 175ms	remaining: 29m 6s
5:	learn: 0.6908749	test: 0.6909125	best: 0.6909125 (5)	total: 209ms	remaining: 29m 1s
6:	learn: 0.6905223	test: 0.6905661	best: 0.6905661 (6)	total: 241ms	remaining: 28m 41s
7:	learn: 0.6901793	test: 0.6902257	best: 0.6902257 (7)	total: 273ms	remaining: 28m 27s
8:	learn: 0.6898357	test: 0.6898938	best: 0.6898938 (8)	total: 304ms	remaining: 28m 8s
9:	learn: 0.6895042	test: 0.6895602	best: 0.6895602 (9)	total: 336ms	remaining: 27m 58s
10:	learn: 0.6891749	test: 0.6892327	best: 0.6892327 (10)	total: 367ms	remaining: 27m 49s
11:	learn: 0.6888600	test: 0.68

99:	learn: 0.6735217	test: 0.6733558	best: 0.6733558 (99)	total: 2.82s	remaining: 23m 29s
100:	learn: 0.6734278	test: 0.6732554	best: 0.6732554 (100)	total: 2.85s	remaining: 23m 27s
101:	learn: 0.6733377	test: 0.6731652	best: 0.6731652 (101)	total: 2.88s	remaining: 23m 26s
102:	learn: 0.6732436	test: 0.6730675	best: 0.6730675 (102)	total: 2.9s	remaining: 23m 25s
103:	learn: 0.6731541	test: 0.6729739	best: 0.6729739 (103)	total: 2.93s	remaining: 23m 24s
104:	learn: 0.6730564	test: 0.6728699	best: 0.6728699 (104)	total: 2.95s	remaining: 23m 24s
105:	learn: 0.6729641	test: 0.6727761	best: 0.6727761 (105)	total: 2.98s	remaining: 23m 23s
106:	learn: 0.6728719	test: 0.6726803	best: 0.6726803 (106)	total: 3.01s	remaining: 23m 24s
107:	learn: 0.6727791	test: 0.6725889	best: 0.6725889 (107)	total: 3.04s	remaining: 23m 24s
108:	learn: 0.6726799	test: 0.6724886	best: 0.6724886 (108)	total: 3.07s	remaining: 23m 23s
109:	learn: 0.6725901	test: 0.6723935	best: 0.6723935 (109)	total: 3.09s	remaining:

193:	learn: 0.6671393	test: 0.6668281	best: 0.6668281 (193)	total: 5.36s	remaining: 22m 55s
194:	learn: 0.6670900	test: 0.6667813	best: 0.6667813 (194)	total: 5.38s	remaining: 22m 55s
195:	learn: 0.6670425	test: 0.6667308	best: 0.6667308 (195)	total: 5.41s	remaining: 22m 54s
196:	learn: 0.6669971	test: 0.6666860	best: 0.6666860 (196)	total: 5.44s	remaining: 22m 54s
197:	learn: 0.6669515	test: 0.6666398	best: 0.6666398 (197)	total: 5.46s	remaining: 22m 54s
198:	learn: 0.6669092	test: 0.6665984	best: 0.6665984 (198)	total: 5.49s	remaining: 22m 53s
199:	learn: 0.6668665	test: 0.6665558	best: 0.6665558 (199)	total: 5.52s	remaining: 22m 53s
200:	learn: 0.6668136	test: 0.6665019	best: 0.6665019 (200)	total: 5.54s	remaining: 22m 53s
201:	learn: 0.6667706	test: 0.6664593	best: 0.6664593 (201)	total: 5.57s	remaining: 22m 53s
202:	learn: 0.6667254	test: 0.6664120	best: 0.6664120 (202)	total: 5.59s	remaining: 22m 52s
203:	learn: 0.6666793	test: 0.6663645	best: 0.6663645 (203)	total: 5.62s	remaini

289:	learn: 0.6635094	test: 0.6632240	best: 0.6632240 (289)	total: 7.9s	remaining: 22m 33s
290:	learn: 0.6634826	test: 0.6631927	best: 0.6631927 (290)	total: 7.92s	remaining: 22m 33s
291:	learn: 0.6634519	test: 0.6631632	best: 0.6631632 (291)	total: 7.95s	remaining: 22m 33s
292:	learn: 0.6634195	test: 0.6631327	best: 0.6631327 (292)	total: 7.97s	remaining: 22m 32s
293:	learn: 0.6633881	test: 0.6631037	best: 0.6631037 (293)	total: 8s	remaining: 22m 32s
294:	learn: 0.6633600	test: 0.6630827	best: 0.6630827 (294)	total: 8.03s	remaining: 22m 32s
295:	learn: 0.6633324	test: 0.6630570	best: 0.6630570 (295)	total: 8.05s	remaining: 22m 31s
296:	learn: 0.6633043	test: 0.6630254	best: 0.6630254 (296)	total: 8.08s	remaining: 22m 31s
297:	learn: 0.6632734	test: 0.6629961	best: 0.6629961 (297)	total: 8.1s	remaining: 22m 31s
298:	learn: 0.6632458	test: 0.6629693	best: 0.6629693 (298)	total: 8.13s	remaining: 22m 31s
299:	learn: 0.6632163	test: 0.6629386	best: 0.6629386 (299)	total: 8.15s	remaining: 2

384:	learn: 0.6609684	test: 0.6607451	best: 0.6607451 (384)	total: 10.4s	remaining: 22m 20s
385:	learn: 0.6609481	test: 0.6607240	best: 0.6607240 (385)	total: 10.5s	remaining: 22m 23s
386:	learn: 0.6609270	test: 0.6607048	best: 0.6607048 (386)	total: 10.5s	remaining: 22m 23s
387:	learn: 0.6609054	test: 0.6606815	best: 0.6606815 (387)	total: 10.5s	remaining: 22m 23s
388:	learn: 0.6608859	test: 0.6606631	best: 0.6606631 (388)	total: 10.5s	remaining: 22m 22s
389:	learn: 0.6608601	test: 0.6606348	best: 0.6606348 (389)	total: 10.6s	remaining: 22m 22s
390:	learn: 0.6608357	test: 0.6606128	best: 0.6606128 (390)	total: 10.6s	remaining: 22m 22s
391:	learn: 0.6608124	test: 0.6605871	best: 0.6605871 (391)	total: 10.6s	remaining: 22m 22s
392:	learn: 0.6607915	test: 0.6605670	best: 0.6605670 (392)	total: 10.6s	remaining: 22m 22s
393:	learn: 0.6607664	test: 0.6605454	best: 0.6605454 (393)	total: 10.7s	remaining: 22m 22s
394:	learn: 0.6607407	test: 0.6605190	best: 0.6605190 (394)	total: 10.7s	remaini

...

49580:	learn: 0.3075687	test: 0.3692484	best: 0.3692484 (49580)	total: 21m 56s	remaining: 11.1s
49581:	learn: 0.3075643	test: 0.3692471	best: 0.3692471 (49581)	total: 21m 56s	remaining: 11.1s
49582:	learn: 0.3075613	test: 0.3692444	best: 0.3692444 (49582)	total: 21m 56s	remaining: 11.1s
49583:	learn: 0.3075569	test: 0.3692391	best: 0.3692391 (49583)	total: 21m 57s	remaining: 11s
49584:	learn: 0.3075521	test: 0.3692323	best: 0.3692323 (49584)	total: 21m 57s	remaining: 11s
49585:	learn: 0.3075491	test: 0.3692297	best: 0.3692297 (49585)	total: 21m 57s	remaining: 11s
49586:	learn: 0.3075446	test: 0.3692270	best: 0.3692270 (49586)	total: 21m 57s	remaining: 11s
49587:	learn: 0.3075388	test: 0.3692173	best: 0.3692173 (49587)	total: 21m 57s	remaining: 10.9s
49588:	learn: 0.3075350	test: 0.3692147	best: 0.3692147 (49588)	total: 21m 57s	remaining: 10.9s
49589:	learn: 0.3075299	test: 0.3692113	best: 0.3692113 (49589)	total: 21m 57s	remaining: 10.9s
49590:	learn: 0.3075268	test: 0.3692090	best: 0.

49668:	learn: 0.3072199	test: 0.3689688	best: 0.3689688 (49668)	total: 21m 59s	remaining: 8.79s
49669:	learn: 0.3072157	test: 0.3689644	best: 0.3689644 (49669)	total: 21m 59s	remaining: 8.77s
49670:	learn: 0.3072131	test: 0.3689623	best: 0.3689623 (49670)	total: 21m 59s	remaining: 8.74s
49671:	learn: 0.3072087	test: 0.3689585	best: 0.3689585 (49671)	total: 21m 59s	remaining: 8.71s
49672:	learn: 0.3072056	test: 0.3689538	best: 0.3689538 (49672)	total: 21m 59s	remaining: 8.69s
49673:	learn: 0.3072015	test: 0.3689512	best: 0.3689512 (49673)	total: 21m 59s	remaining: 8.66s
49674:	learn: 0.3071969	test: 0.3689479	best: 0.3689479 (49674)	total: 21m 59s	remaining: 8.63s
49675:	learn: 0.3071918	test: 0.3689433	best: 0.3689433 (49675)	total: 21m 59s	remaining: 8.61s
49676:	learn: 0.3071884	test: 0.3689408	best: 0.3689408 (49676)	total: 21m 59s	remaining: 8.58s
49677:	learn: 0.3071850	test: 0.3689352	best: 0.3689352 (49677)	total: 21m 59s	remaining: 8.55s
49678:	learn: 0.3071805	test: 0.3689324	

49756:	learn: 0.3068817	test: 0.3687054	best: 0.3687054 (49756)	total: 22m 1s	remaining: 6.45s
49757:	learn: 0.3068761	test: 0.3686988	best: 0.3686988 (49757)	total: 22m 1s	remaining: 6.43s
49758:	learn: 0.3068703	test: 0.3686942	best: 0.3686942 (49758)	total: 22m 1s	remaining: 6.4s
49759:	learn: 0.3068669	test: 0.3686901	best: 0.3686901 (49759)	total: 22m 1s	remaining: 6.38s
49760:	learn: 0.3068624	test: 0.3686876	best: 0.3686876 (49760)	total: 22m 1s	remaining: 6.35s
49761:	learn: 0.3068591	test: 0.3686848	best: 0.3686848 (49761)	total: 22m 1s	remaining: 6.32s
49762:	learn: 0.3068553	test: 0.3686821	best: 0.3686821 (49762)	total: 22m 1s	remaining: 6.29s
49763:	learn: 0.3068522	test: 0.3686804	best: 0.3686804 (49763)	total: 22m 1s	remaining: 6.27s
49764:	learn: 0.3068482	test: 0.3686773	best: 0.3686773 (49764)	total: 22m 1s	remaining: 6.24s
49765:	learn: 0.3068437	test: 0.3686738	best: 0.3686738 (49765)	total: 22m 1s	remaining: 6.21s
49766:	learn: 0.3068405	test: 0.3686714	best: 0.368

49844:	learn: 0.3065385	test: 0.3684294	best: 0.3684294 (49844)	total: 22m 4s	remaining: 4.12s
49845:	learn: 0.3065351	test: 0.3684258	best: 0.3684258 (49845)	total: 22m 4s	remaining: 4.09s
49846:	learn: 0.3065318	test: 0.3684238	best: 0.3684238 (49846)	total: 22m 4s	remaining: 4.06s
49847:	learn: 0.3065282	test: 0.3684205	best: 0.3684205 (49847)	total: 22m 4s	remaining: 4.04s
49848:	learn: 0.3065245	test: 0.3684177	best: 0.3684177 (49848)	total: 22m 4s	remaining: 4.01s
49849:	learn: 0.3065203	test: 0.3684156	best: 0.3684156 (49849)	total: 22m 4s	remaining: 3.98s
49850:	learn: 0.3065158	test: 0.3684120	best: 0.3684120 (49850)	total: 22m 4s	remaining: 3.96s
49851:	learn: 0.3065107	test: 0.3684072	best: 0.3684072 (49851)	total: 22m 4s	remaining: 3.93s
49852:	learn: 0.3065061	test: 0.3684047	best: 0.3684047 (49852)	total: 22m 4s	remaining: 3.9s
49853:	learn: 0.3065011	test: 0.3684010	best: 0.3684010 (49853)	total: 22m 4s	remaining: 3.88s
49854:	learn: 0.3064973	test: 0.3683974	best: 0.368

49932:	learn: 0.3061971	test: 0.3681505	best: 0.3681505 (49932)	total: 22m 6s	remaining: 1.78s
49933:	learn: 0.3061940	test: 0.3681484	best: 0.3681484 (49933)	total: 22m 6s	remaining: 1.75s
49934:	learn: 0.3061900	test: 0.3681458	best: 0.3681458 (49934)	total: 22m 6s	remaining: 1.73s
49935:	learn: 0.3061865	test: 0.3681439	best: 0.3681439 (49935)	total: 22m 6s	remaining: 1.7s
49936:	learn: 0.3061826	test: 0.3681396	best: 0.3681396 (49936)	total: 22m 6s	remaining: 1.67s
49937:	learn: 0.3061785	test: 0.3681358	best: 0.3681358 (49937)	total: 22m 6s	remaining: 1.65s
49938:	learn: 0.3061747	test: 0.3681325	best: 0.3681325 (49938)	total: 22m 6s	remaining: 1.62s
49939:	learn: 0.3061709	test: 0.3681309	best: 0.3681309 (49939)	total: 22m 6s	remaining: 1.59s
49940:	learn: 0.3061665	test: 0.3681283	best: 0.3681283 (49940)	total: 22m 6s	remaining: 1.57s
49941:	learn: 0.3061637	test: 0.3681264	best: 0.3681264 (49941)	total: 22m 6s	remaining: 1.54s
49942:	learn: 0.3061601	test: 0.3681229	best: 0.368

In [12]:
print(cat_model.score(x_val,y_val))

0.898758389261745


In [13]:
ypred = cat_model.predict(x_val)
m=n=0
for i in range(len(ypred)):
    if ypred[i] == 0:
        m+=1
    else:
        n+=1
print(n)

4536


In [14]:
for i in range(len(y_val)):
    if y_val.iloc[i] == 0:
        m+=1
    else:
        n+=1
print(n)

6654


In [15]:
y_need = cat_model.predict(test)

In [16]:
for i in range(len(y_need)):
    if y_need[i] == 0:
        m+=1
    else:
        n+=1
print(n)

6808


In [18]:
y_proba = cat_model.predict_proba(test)

In [22]:
result = pd.DataFrame(data=y_proba, index=test.index)

In [23]:
result.shape

(892816, 2)

In [24]:
result.to_csv("finalsub.csv")